In [1]:
!pip install diffusers transformers accelerate safetensors

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 12.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 47.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 261.0/261.0 kB 31.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 64.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.0/302.0 kB 38.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 89.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 37.3 MB/s eta 0:00:00


In [ ]:
!pip install pyngrok

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 718.7/718.7 kB 10.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyngrok: filename=pyngrok-7.0.0-py3-none-any.whl size=21129 sha256=b7c25cb798d2dbb0a15dae8b67762a7922787c50db29379dbedd5be5c8c16c1d
  Stored in directory: /root/.cache/pip/wheels/60/29/7b/f64332aa7e5e88fbd56d4002185ae22dcdc83b35b3d1c2cbf5
Successfully built pyngrok


In [ ]:
# !kill 30402
# !kill 2056
!ps

    PID TTY          TIME CMD
      1 ?        00:00:00 docker-init
      7 ?        00:00:15 node
     18 ?        00:00:01 oom_monitor.sh
     20 ?        00:00:00 run.sh
     22 ?        00:00:02 kernel_manager_
     37 ?        00:00:00 tail
     56 ?        00:00:05 python3 <defunct>
     57 ?        00:00:00 colab-fileshim.
    102 ?        00:00:11 jupyter-noteboo
    106 ?        00:00:03 dap_multiplexer
  13434 ?        00:00:24 python3
  14319 ?        00:00:00 language_servic
  14325 ?        00:00:36 node
  16072 ?        00:00:00 sleep
  16073 ?        00:00:00 ps


In [ ]:
import getpass

from pyngrok import ngrok, conf

print("Enter your authtoken, which can be copied from https://dashboard.ngrok.com/auth")
conf.get_default().auth_token = "2XPL4pgzgjUheG4Jy1ecmjuBocF_2k3qcfEmmgBMgdeRKvTXT"

# Open a TCP ngrok tunnel to the SSH server
connection_string = ngrok.connect("22", "tcp").public_url

ssh_url, port = connection_string.strip("tcp://").split(":")
print(f" * ngrok tunnel available, access with `ssh root@{ssh_url} -p{port}`")

Enter your authtoken, which can be copied from https://dashboard.ngrok.com/auth


 * ngrok tunnel available, access with `ssh root@0.tcp.ngrok.io -p19395`


In [ ]:
taskkill /f /im ngrok.exe


SyntaxError: ignored

In [2]:
!pip install opencv-contrib-python

In [3]:
from diffusers import StableDiffusionImg2ImgPipeline
from diffusers import StableDiffusionControlNetImg2ImgPipeline, ControlNetModel
import torch
from diffusers import DPMSolverMultistepScheduler
from PIL import Image
import cv2
import numpy as np


controlnet = ControlNetModel.from_pretrained("lllyasviel/sd-controlnet-canny", torch_dtype=torch.float16)
pipe = StableDiffusionControlNetImg2ImgPipeline.from_pretrained(
    "stablediffusionapi/realistic-vision-v51", controlnet=controlnet, torch_dtype=torch.float16
)
pipe.to("cuda")
components = {k: v for k, v in pipe.components.items() if k != "controlnet"}
pipe = StableDiffusionImg2ImgPipeline(**components)

pipe.scheduler = DPMSolverMultistepScheduler.from_config(pipe.scheduler.config, use_karras=True, algorithm_type="sde-dpmsolver++")

controlnet2 = ControlNetModel.from_pretrained("lllyasviel/sd-controlnet-canny", torch_dtype=torch.float16)
pipe2 = StableDiffusionControlNetImg2ImgPipeline.from_pretrained(
    "stablediffusionapi/realistic-vision-v51", controlnet=controlnet2, torch_dtype=torch.float16
)
pipe2.to("cuda")
components2 = {k: v for k, v in pipe2.components.items() if k != "controlnet"}
pipe2 = StableDiffusionImg2ImgPipeline(**components2)

pipe2.scheduler = DPMSolverMultistepScheduler.from_config(pipe2.scheduler.config, use_karras=True, algorithm_type="sde-dpmsolver++")
final_pipe_line = StableDiffusionControlNetImg2ImgPipeline(**components2, controlnet=controlnet2)

def process_image(image,prompt,negative_prompt):
    processed_image = pipe(prompt=prompt, negative_prompt=negative_prompt, image=image, strength=0.38, num_inference_steps=40, guidance_scale=8).images[0]
    return processed_image
def process_image2(image,prompt,negative_prompt):
    processed_image = pipe2(prompt=prompt, negative_prompt=negative_prompt, image=image, strength=0.38, num_inference_steps=40, guidance_scale=8).images[0]
    return processed_image

def process_filters(image):
    canny_image = np.array(image)
    low_threshold = 100
    high_threshold = 200

    canny_image = cv2.Canny(canny_image, low_threshold, high_threshold)
    canny_image = canny_image[:, :, None]
    canny_image = np.concatenate([canny_image, canny_image, canny_image], axis=2)
    canny_image = Image.fromarray(canny_image)
    return canny_image

def process_image_final(image,control_image,prompt,negative_prompt):

    processed_image = final_pipe_line(prompt=prompt, negative_prompt=negative_prompt, image=image, control_image=control_image, strength=0.5).images[0]
    return processed_image

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

unet/diffusion_pytorch_model.safetensors not found


Fetching 15 files:   0%|          | 0/15 [00:00<?, ?it/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
unet/diffusion_pytorch_model.safetensors not found


Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

In [4]:
import os
#code to run
# def images_process():

# Get the path to the video file.
video_path = "/content/video2.mp4"

# Open the video file.
vidcap = cv2.VideoCapture(video_path)

# # Get the length of the video.
length = int(vidcap.get(cv2.CAP_PROP_FRAME_COUNT))

# Create a list to store the frames.
# frames = []
success = True

count=0
path = "/content/results"
os.makedirs(path, exist_ok=True)
# Read each frame from the video file.
while success:
  success, image = vidcap.read()
  # Save the frame as a JPEG file.
  cv2.imwrite(os.path.join(path, "frame_%d_input.jpg" % count), image)

  # Process the frame using the fusion model functions.
  prompt = "temporal consistency,traffic congested indian street with cattle blocking the road and vegetable vendors on the roadside realistic image, deep contrast,green grass side path"
  negative_prompt = "NSFW,Disfigured, cartoon, blurry,no dusty environment,no nudes, sketch, cartoon, drawing, anime, mutated hands and fingers, (deformed, distorted, disfigured:1.3), poorly drawn, bad anatomy, wrong anatomy, extra limb, missing limb, floating limbs, disconnected limbs, mutation, mutated, ugly, disgusting, amputation"

    # img = Image.open(os.path.join(path, "frame_%d_input.jpg" % count))
  one_step = process_image(image, prompt, negative_prompt)
  second_step= process_image2(one_step, prompt, negative_prompt)
  control = process_filters(second_step)
  final_image = process_image_final(second_step, control, prompt, negative_prompt)

  # Save the processed frame to the directory.
  final_image.save(os.path.join(path, "frame_%d_processed.jpg" % count))
  count+=1
  print(count)


  0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

Potential NSFW content was detected in one or more images. A black image will be returned instead. Try again with a different prompt and/or seed.


  0%|          | 0/25 [00:00<?, ?it/s]

Potential NSFW content was detected in one or more images. A black image will be returned instead. Try again with a different prompt and/or seed.


...

  0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/25 [00:00<?, ?it/s]

154


error: ignored

In [5]:
!zip -r /content/results.zip /content/results

  adding: content/results/ (stored 0%)
  adding: content/results/frame_22_processed.jpg (deflated 2%)
  adding: content/results/frame_120_processed.jpg (deflated 1%)
  adding: content/results/frame_64_input.jpg (deflated 0%)
  adding: content/results/frame_88_processed.jpg (deflated 1%)
  adding: content/results/frame_53_input.jpg (deflated 0%)
  adding: content/results/frame_143_input.jpg (deflated 0%)
  adding: content/results/frame_27_input.jpg (deflated 0%)
  adding: content/results/frame_114_processed.jpg (deflated 1%)
  adding: content/results/frame_136_input.jpg (deflated 0%)
  adding: content/results/frame_0_input.jpg (deflated 94%)
  adding: content/results/frame_152_input.jpg (deflated 0%)
  adding: content/results/frame_51_input.jpg (deflated 0%)
  adding: content/results/frame_108_processed.jpg (deflated 1%)
  adding: content/results/frame_116_input.jpg (deflated 0%)
  adding: content/results/frame_40_input.jpg (deflated 0%)
  adding: content/results/frame_35_input.jpg (def